In [37]:
import os
os.environ['CUDA_VISIBLEDEVICES'] = ''
os.environ['KERAS_BACKEND'] = 'theano'
from keras.models import model_from_json
from keras import backend as K
from deeplift.conversion import keras_conversion as kc
from tfdragonn.interpretation.dl_conversion_funcs import permute_conversion, reshape_conversion
from deeplift.blobs.core import NonlinearMxtsMode
import numpy as np

In [9]:
arch_json = "/srv/scratch/tfbinding/tf_logs/genome_wide/single_celltype/seq_dnase_baselines/v0.1/trial-3/A549/CEBPB/model.arch.json"
weights_h5 = "/srv/scratch/tfbinding/tf_logs/genome_wide/single_celltype/seq_dnase_baselines/v0.1/trial-3/A549/CEBPB/model.weights.h5"

In [10]:
model_json = open(arch_json, 'r').read()
## replace -1 concat axes to 2 because
## deeplift doesnt convert correct a -1 concat axis
model_json = model_json.replace('"concat_axis": -1', '"concat_axis": 2')
keras_model = model_from_json(model_json)
keras_model.load_weights(weights_h5)

In [11]:
conversion_funcs = {'Permute': permute_conversion,
                    'Reshape': reshape_conversion}

In [12]:
deeplift_model = kc.convert_functional_model(keras_model,
                                             nonlinear_mxts_mode=NonlinearMxtsMode.DeepLIFT_GenomicsDefault,
                                             custom_conversion_funcs=conversion_funcs)

nonlinear_mxts_mode is set to: DeepLIFT_GenomicsDefault
For layer activation_1 the preceding linear layer is convolution1d_2 of type Conv1D;
In accordance with nonlinear_mxts_mode=DeepLIFT_GenomicsDefault we are setting the NonlinearMxtsMode to Rescale
For layer activation_2 the preceding linear layer is convolution1d_3 of type Conv1D;
In accordance with nonlinear_mxts_mode=DeepLIFT_GenomicsDefault we are setting the NonlinearMxtsMode to Rescale
For layer activation_3 the preceding linear layer is convolution1d_4 of type Conv1D;
In accordance with nonlinear_mxts_mode=DeepLIFT_GenomicsDefault we are setting the NonlinearMxtsMode to Rescale
For layer activation_4 the preceding linear layer is convolution1d_5 of type Conv1D;
In accordance with nonlinear_mxts_mode=DeepLIFT_GenomicsDefault we are setting the NonlinearMxtsMode to Rescale
For layer activation_5 the preceding linear layer is convolution1d_6 of type Conv1D;
In accordance with nonlinear_mxts_mode=DeepLIFT_GenomicsDefault we are 

In [13]:
score_funcs = {input_name: deeplift_model.get_target_contribs_func(input_name, keras_model.layers[-2].name) 
               for input_name in keras_model.input_names} # layers[-2] should be the target layer

In [15]:
from pybedtools import Interval
intervals = [Interval('chr6', 36562700, 36563700)]

In [16]:
from genomelake.extractors import ArrayExtractor

In [17]:
seq_extractor = ArrayExtractor("/srv/scratch/genomelake_data/hg19.genome.fa/")
dnase_extractor = ArrayExtractor("/srv/scratch/genomelake_data/DNASE.A549.fc.signal.bigwig/")

In [18]:
seq_data = seq_extractor(intervals)

In [19]:
dnase_data = dnase_extractor(intervals)

In [20]:
seq_data.shape

(1, 1000, 4)

In [21]:
dnase_data.shape

(1, 1000)

In [24]:
seq_data = np.swapaxes(seq_data, 1, 2)

In [26]:
seq_data.shape

(1, 4, 1000)

In [25]:
keras_model.input_names

[u'data/genome_data_dir', u'data/dnase_data_dir']

In [28]:
reference_dict = {'data/genome_data_dir': np.zeros((4, 1000))[None, :],
                  'data/dnase_data_dir': np.zeros((1000))[None, :]}

In [30]:
batch = {'data/genome_data_dir': seq_data,
         'data/dnase_data_dir': dnase_data}

In [31]:
scores = {input_name: score_func(task_idx=0, input_data_list=batch,
                                 input_references_list=reference_dict,
                                 batch_size=1, progress_update=None)
          for input_name, score_func in score_funcs.items()}

In [32]:
scores.keys()

[u'data/dnase_data_dir', u'data/genome_data_dir']

In [34]:
scores['data/genome_data_dir'][0].shape

(4, 1000)

In [35]:
scores['data/dnase_data_dir'][0].shape

(1000,)

In [38]:
K.gradients?

In [43]:
keras_model.layers

In [46]:
output_scalar = keras_model.layers[-2].output.sum()

In [47]:
grad_seq_func = K.gradients(output_scalar, keras_model.layers[0].input)

In [62]:
K.dot?

In [63]:
seq_input_times_grad = grad_seq_func * keras_model.layers[0].input

In [64]:
grad_seq_func_theano = K.function([keras_model.layers[0].input, keras_model.layers[1].input],
                                  [seq_input_times_grad])

In [65]:
res = grad_seq_func_theano([batch['data/genome_data_dir'], batch['data/dnase_data_dir']])

In [66]:
res[0].shape

(1, 4, 1000)

In [67]:
np.max(np.absolute(scores['data/genome_data_dir'][0] - res[0][0]))

1.7407913

In [68]:
keras_model.predict(batch)

array([[ 0.02015416]], dtype=float32)

In [69]:
def set_keras_backend(backend):

    if K.backend() != backend:
        os.environ['KERAS_BACKEND'] = backend
        reload(K)
    assert K.backend() == backend

In [70]:
set_keras_backend('tensorflow')

Using TensorFlow backend.


In [ ]:
keras_model_tf = model_from_json(model_json)
keras_model_tf.load_weights(weights_h5)